# Классификация: Логистическая регрессия и SVM

Педсказание уровня дохода на основе дата сета при помощии логистической регресии и SVM. Ожидаемый выходной ответ: доход  '>50K' или '<=50K'.

##  1. Импорт необходимых библиотек

In [112]:
!pip install https://github.com/pandas-profiling/pandas-profiling/archive/master.zip
!pip install xlwt

  Using cached https://github.com/pandas-profiling/pandas-profiling/archive/master.zip
  Preparing metadata (setup.py) ... done
     |████████████████████████████████| 99 kB 1.0 MB/s            


In [127]:
import pandas as pd
import numpy as np
from pandas_profiling import ProfileReport
from sklearn.linear_model import LogisticRegression
from sklearn.pipeline import make_pipeline
from sklearn.compose import make_column_transformer
from sklearn.compose import make_column_selector
from sklearn.preprocessing import OneHotEncoder
from sklearn.preprocessing import LabelEncoder
from sklearn.model_selection import train_test_split
from sklearn.metrics import r2_score
from sklearn.preprocessing import StandardScaler
from sklearn.svm import SVC

In [ ]:
data=pd.read_csv('prep_adult.csv')
data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 41657 entries, 0 to 41656
Data columns (total 12 columns):
 #   Column          Non-Null Count  Dtype 
---  ------          --------------  ----- 
 0   age             41657 non-null  int64 
 1   workclass       41657 non-null  object
 2   education       41657 non-null  object
 3   occupation      41657 non-null  object
 4   relationship    41657 non-null  object
 5   race            41657 non-null  object
 6   gender          41657 non-null  object
 7   capital-gain    41657 non-null  int64 
 8   capital-loss    41657 non-null  int64 
 9   hours-per-week  41657 non-null  int64 
 10  native-country  41657 non-null  object
 11  income          41657 non-null  object
dtypes: int64(4), object(8)
memory usage: 3.8+ MB


## 2. Импорт и предобработка данных

In [80]:
df=pd.read_csv('adult.csv')
df.head()

age  workclass  fnlwgt     education  educational-num      marital-status  \
0   25    Private  226802          11th                7       Never-married   
1   38    Private   89814       HS-grad                9  Married-civ-spouse   
2   28  Local-gov  336951    Assoc-acdm               12  Married-civ-spouse   
3   44    Private  160323  Some-college               10  Married-civ-spouse   
4   18          ?  103497  Some-college               10       Never-married   

          occupation relationship   race  gender  capital-gain  capital-loss  \
0  Machine-op-inspct    Own-child  Black    Male             0             0   
1    Farming-fishing      Husband  White    Male             0             0   
2    Protective-serv      Husband  White    Male             0             0   
3  Machine-op-inspct      Husband  Black    Male          7688             0   
4                  ?    Own-child  White  Female             0             0   

   hours-per-week native-country income  
0              40  United-States  <=50K  
1              50  United-States  <=50K  
2              40  United-States   >50K  
3              40  United-States   >50K  
4              30  United-States  <=50K

In [81]:
#Размерност данных
df.shape

(48842, 15)

In [82]:
profile=ProfileReport(df, title="Adult", html={'style':{'full_width': True}})
profile.to_file(output_file="Adult")
profile.to_notebook_iframe()

Render HTML: 100%|██████████| 1/1 [00:00<00:00,  1.55it/s]
/Users/valentincyganok/miniforge3/envs/env_tensorflow/lib/python3.9/site-packages/pandas_profiling/profile_report.py:262: UserWarning: Extension  not supported. For now we assume .html was intended. To remove this warning, please use .html or .json.
  warnings.warn(
Export report to file: 100%|██████████| 1/1 [00:00<00:00, 205.33it/s]


In [83]:
df=df.drop(columns=['marital-status','fnlwgt','educational-num',])
df.drop_duplicates(inplace=True)
df.head()

age  workclass     education         occupation relationship   race  \
0   25    Private          11th  Machine-op-inspct    Own-child  Black   
1   38    Private       HS-grad    Farming-fishing      Husband  White   
2   28  Local-gov    Assoc-acdm    Protective-serv      Husband  White   
3   44    Private  Some-college  Machine-op-inspct      Husband  Black   
4   18          ?  Some-college                  ?    Own-child  White   

   gender  capital-gain  capital-loss  hours-per-week native-country income  
0    Male             0             0              40  United-States  <=50K  
1    Male             0             0              50  United-States  <=50K  
2    Male             0             0              40  United-States   >50K  
3    Male          7688             0              40  United-States   >50K  
4  Female             0             0              30  United-States  <=50K

In [84]:
df.replace('?','Unknow',inplace=True)
df.head()

age  workclass     education         occupation relationship   race  \
0   25    Private          11th  Machine-op-inspct    Own-child  Black   
1   38    Private       HS-grad    Farming-fishing      Husband  White   
2   28  Local-gov    Assoc-acdm    Protective-serv      Husband  White   
3   44    Private  Some-college  Machine-op-inspct      Husband  Black   
4   18     Unknow  Some-college             Unknow    Own-child  White   

   gender  capital-gain  capital-loss  hours-per-week native-country income  
0    Male             0             0              40  United-States  <=50K  
1    Male             0             0              50  United-States  <=50K  
2    Male             0             0              40  United-States   >50K  
3    Male          7688             0              40  United-States   >50K  
4  Female             0             0              30  United-States  <=50K

In [85]:
profile=ProfileReport(df, title="Adult", html={'style':{'full_width': True}})
profile.to_file(output_file="Adult")

Render HTML: 100%|██████████| 1/1 [00:00<00:00,  2.02it/s]
/Users/valentincyganok/miniforge3/envs/env_tensorflow/lib/python3.9/site-packages/pandas_profiling/profile_report.py:262: UserWarning: Extension  not supported. For now we assume .html was intended. To remove this warning, please use .html or .json.
  warnings.warn(
Export report to file: 100%|██████████| 1/1 [00:00<00:00, 382.94it/s]


In [86]:
df.to_csv('prep_adult.csv',index=False)

## 3. Логистическая регрессия 

In [131]:
data=pd.read_csv('prep_adult.csv')
data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 41657 entries, 0 to 41656
Data columns (total 12 columns):
 #   Column          Non-Null Count  Dtype 
---  ------          --------------  ----- 
 0   age             41657 non-null  int64 
 1   workclass       41657 non-null  object
 2   education       41657 non-null  object
 3   occupation      41657 non-null  object
 4   relationship    41657 non-null  object
 5   race            41657 non-null  object
 6   gender          41657 non-null  object
 7   capital-gain    41657 non-null  int64 
 8   capital-loss    41657 non-null  int64 
 9   hours-per-week  41657 non-null  int64 
 10  native-country  41657 non-null  object
 11  income          41657 non-null  object
dtypes: int64(4), object(8)
memory usage: 3.8+ MB


In [96]:
data.head()

age  workclass     education         occupation relationship   race  \
0   25    Private          11th  Machine-op-inspct    Own-child  Black   
1   38    Private       HS-grad    Farming-fishing      Husband  White   
2   28  Local-gov    Assoc-acdm    Protective-serv      Husband  White   
3   44    Private  Some-college  Machine-op-inspct      Husband  Black   
4   18     Unknow  Some-college             Unknow    Own-child  White   

   gender  capital-gain  capital-loss  hours-per-week native-country income  
0    Male             0             0              40  United-States  <=50K  
1    Male             0             0              50  United-States  <=50K  
2    Male             0             0              40  United-States   >50K  
3    Male          7688             0              40  United-States   >50K  
4  Female             0             0              30  United-States  <=50K

In [132]:
X=data.drop('income',axis=1)
y=data['income']
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

In [103]:
one_hot_encoder=make_column_transformer(
    (
        StandardScaler(),
        make_column_selector(dtype_include="int64"),
    ),
    (
        OneHotEncoder(sparse=True, handle_unknown="ignore"),
        make_column_selector(dtype_include="object"),
    ),
    remainder="passthrough",
)
logistis_reg = make_pipeline(one_hot_encoder,LogisticRegression(max_iter=10000))
logistis_reg.fit(X_train, y_train)

Pipeline(steps=[('columntransformer',
                 ColumnTransformer(remainder='passthrough',
                                   transformers=[('standardscaler',
                                                  StandardScaler(),
                                                  <sklearn.compose._column_transformer.make_column_selector object at 0x286e82190>),
                                                 ('onehotencoder',
                                                  OneHotEncoder(handle_unknown='ignore'),
                                                  <sklearn.compose._column_transformer.make_column_selector object at 0x286e821c0>)])),
                ('logisticregression', LogisticRegression(max_iter=10000))])

In [133]:
logistis_reg.score(X_test,y_test)

0.8451752280364858

На новых данных, точность предсказания достигла 84%.

In [134]:
data['predict_income']=logistis_reg.predict(data)
data.to_excel('pred_results_Adult(Log).xls',index=False)

/Users/valentincyganok/miniforge3/envs/env_tensorflow/lib/python3.9/site-packages/sklearn/compose/_column_transformer.py:437: FutureWarning: Given feature/column names or counts do not match the ones for the data given during fit. This will fail from v0.24.
  warnings.warn("Given feature/column names or counts do not match "
/var/folders/h3/74c4hrxx0rv2_bhxxlprp7t80000gn/T/ipykernel_71466/3627465593.py:2: FutureWarning: As the xlwt package is no longer maintained, the xlwt engine will be removed in a future version of pandas. This is the only engine in pandas that supports writing in the xls format. Install openpyxl and write to an xlsx file instead. You can set the option io.excel.xls.writer to 'xlwt' to silence this warning. While this option is deprecated and will also raise a warning, it can be globally set and the warning suppressed.
  data.to_excel('pred_results_Adult(Log).xls',index=False)


# SVM

In [135]:
data=pd.read_csv('prep_adult.csv')
data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 41657 entries, 0 to 41656
Data columns (total 12 columns):
 #   Column          Non-Null Count  Dtype 
---  ------          --------------  ----- 
 0   age             41657 non-null  int64 
 1   workclass       41657 non-null  object
 2   education       41657 non-null  object
 3   occupation      41657 non-null  object
 4   relationship    41657 non-null  object
 5   race            41657 non-null  object
 6   gender          41657 non-null  object
 7   capital-gain    41657 non-null  int64 
 8   capital-loss    41657 non-null  int64 
 9   hours-per-week  41657 non-null  int64 
 10  native-country  41657 non-null  object
 11  income          41657 non-null  object
dtypes: int64(4), object(8)
memory usage: 3.8+ MB


In [124]:
data.head()

age  workclass     education         occupation relationship   race  \
0   25    Private          11th  Machine-op-inspct    Own-child  Black   
1   38    Private       HS-grad    Farming-fishing      Husband  White   
2   28  Local-gov    Assoc-acdm    Protective-serv      Husband  White   
3   44    Private  Some-college  Machine-op-inspct      Husband  Black   
4   18     Unknow  Some-college             Unknow    Own-child  White   

   gender  capital-gain  capital-loss  hours-per-week native-country income  
0    Male             0             0              40  United-States  <=50K  
1    Male             0             0              50  United-States  <=50K  
2    Male             0             0              40  United-States   >50K  
3    Male          7688             0              40  United-States   >50K  
4  Female             0             0              30  United-States  <=50K

In [125]:
X=data.drop('income',axis=1)
y=data['income']
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

In [128]:
one_hot_encoder=make_column_transformer(
    (
        StandardScaler(),
        make_column_selector(dtype_include="int64"),
    ),
    (
        OneHotEncoder(sparse=True, handle_unknown="ignore"),
        make_column_selector(dtype_include="object"),
    ),
    remainder="passthrough",
)
SVM_reg = make_pipeline(one_hot_encoder, SVC(gamma='auto'))
SVM_reg.fit(X_train, y_train)

Pipeline(steps=[('columntransformer',
                 ColumnTransformer(remainder='passthrough',
                                   transformers=[('standardscaler',
                                                  StandardScaler(),
                                                  <sklearn.compose._column_transformer.make_column_selector object at 0x2866a0fa0>),
                                                 ('onehotencoder',
                                                  OneHotEncoder(handle_unknown='ignore'),
                                                  <sklearn.compose._column_transformer.make_column_selector object at 0x2866a0970>)])),
                ('svc', SVC(gamma='auto'))])

In [136]:
SVM_reg.score(X_test,y_test)

0.8509361497839655

На новых данных, точность предсказания достигла 85%. Прирост  точности составил 1%, а время предсказания в 3 раза выше по сравнению с логистической регресией. Для предоставленных данных рекомендую использовать - логистическую регрессию.

In [137]:
data['predict_income']=logistis_reg.predict(data)
data.to_excel('pred_results_Adult(SVM).xls',index=False)

/Users/valentincyganok/miniforge3/envs/env_tensorflow/lib/python3.9/site-packages/sklearn/compose/_column_transformer.py:437: FutureWarning: Given feature/column names or counts do not match the ones for the data given during fit. This will fail from v0.24.
  warnings.warn("Given feature/column names or counts do not match "
/var/folders/h3/74c4hrxx0rv2_bhxxlprp7t80000gn/T/ipykernel_71466/785567433.py:2: FutureWarning: As the xlwt package is no longer maintained, the xlwt engine will be removed in a future version of pandas. This is the only engine in pandas that supports writing in the xls format. Install openpyxl and write to an xlsx file instead. You can set the option io.excel.xls.writer to 'xlwt' to silence this warning. While this option is deprecated and will also raise a warning, it can be globally set and the warning suppressed.
  data.to_excel('pred_results_Adult(SVM).xls',index=False)
